In [1]:
%load_ext rpy2.ipython

In [32]:
%%R
set.seed(88888888) # maximum luck

library(DESeq2)
library(plotly)
library(ggplot2)
library(viridis)
library(magrittr)
library(pheatmap)
library(DescTools)
library(pdfCluster)
library(RColorBrewer)
library(SummarizedExperiment)
library(caret)
library(class)
library(htmlwidgets)

In [33]:
%%R
OUT_DIR <- "/mnt/home/yuankeji/RanceLab/reticula_new/reticula/data/tcdd/learning_curve_analysis/output/"
N_FOLDS <- 10

In [34]:
%%R
vst.counts <- readRDS(paste(OUT_DIR, "vst_counts030_time_cross_60.Rds", sep = ""))
print(vst.counts)

class: DESeqTransform 
dim: 9297 80 
metadata(1): version
assays(1): ''
rownames(9297): ENSMUSG00000000001 ENSMUSG00000000028 ...
  ENSMUSG00000118462 ENSMUSG00000118541
rowData names(4): baseMean baseVar allZero dispFit
colnames(80): SRR7817659 SRR7817662 ... SRR7817679 SRR3593580
colData names(3): Sample Dose sizeFactor


In [35]:
%%R
sample <- colData(vst.counts)
# print(sample)

In [36]:
%%R
vst.count.mtx <-
   vst.counts %>% SummarizedExperiment::assay() %>% as.data.frame()
print(length(vst.count.mtx))
 head(vst.count.mtx)

[1] 80
                   SRR7817659 SRR7817662 SRR1636592 SRR1636589 SRR7817700
ENSMUSG00000000001  15.923589  15.884339  16.443794  16.193522  15.912485
ENSMUSG00000000028   7.902323   7.607930   7.444365   7.354297   8.081032
ENSMUSG00000000049  20.134973  20.441851  20.511097  20.538200  20.195334
ENSMUSG00000000058   8.116307   8.248950   9.692393   9.012625   8.162379
ENSMUSG00000000085  10.738549   9.984175  10.100215   9.927540  10.185008
ENSMUSG00000000088  16.259646  16.872422  16.073736  15.938898  16.840031
                   SRR7817675 SRR7817695 SRR7817699 SRR3593527 SRR7817616
ENSMUSG00000000001  15.791341  15.868255  15.904752  15.079699  15.683604
ENSMUSG00000000028   7.698459   6.725611   7.510894   7.838520   7.364069
ENSMUSG00000000049  20.025093  20.086266  20.180036  20.941676  20.382103
ENSMUSG00000000058   8.844139   8.413413   8.018204   8.049605   8.865917
ENSMUSG00000000085   9.964090  10.663237  10.745341  10.842703  10.177832
ENSMUSG00000000088  16.696660  

ENSMUSG00000000085  10.978726  11.020998  10.911086  11.168165  10.718945
ENSMUSG00000000088  16.354252  16.707520  16.027239  15.801387  15.034174


In [37]:
%%R
tcdd_dose_detail.vec <-
   readRDS(paste(OUT_DIR, "tcdd_dose_detail_vec030_time_cross_60.Rds", sep = ""))
print(tcdd_dose_detail.vec)

 [1]  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
[26]  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0 30 30 30 30 30 30 30 30 30 30
[51] 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30 30
[76] 30 30 30 30 30


In [38]:
%%R
rxn2ensembls.nls <-
   readRDS(paste(OUT_DIR, "rxn2ensembls_nls030_time_cross_60.Rds", sep = ""))
print(length(rxn2ensembls.nls))
print(rxn2ensembls.nls)

[1] 9825
$`R-MMU-170666`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170671`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSMUSG00000057614"

$`R-MMU-170674`
 [1] "ENSMUSG00000000001" "ENSMUSG00000005580" "ENSMUSG00000020431"
 [4] "ENSMUSG00000020654" "ENSMUSG00000021536" "ENSMUSG00000022220"
 [7] "ENSMUSG00000022376" "ENSMUSG00000022840" "ENSMUSG00000022994"
[10] "ENSMUSG00000024524" "ENSMUSG00000028777" "ENSMUSG00000031659"
[13] "ENSMUSG00000032562" "ENSM

 [46] "ENSMUSG00000028777" "ENSMUSG00000028950" "ENSMUSG00000028971"
 [49] "ENSMUSG00000029064" "ENSMUSG00000029072" "ENSMUSG00000029236"
 [52] "ENSMUSG00000029371" "ENSMUSG00000029372" "ENSMUSG00000029373"
 [55] "ENSMUSG00000029379" "ENSMUSG00000029380" "ENSMUSG00000029417"
 [58] "ENSMUSG00000029530" "ENSMUSG00000029663" "ENSMUSG00000029713"
 [61] "ENSMUSG00000029819" "ENSMUSG00000031778" "ENSMUSG00000031861"
 [64] "ENSMUSG00000031980" "ENSMUSG00000032192" "ENSMUSG00000032562"
 [67] "ENSMUSG00000032766" "ENSMUSG00000033717" "ENSMUSG00000034117"
 [70] "ENSMUSG00000034855" "ENSMUSG00000035042" "ENSMUSG00000035383"
 [73] "ENSMUSG00000035431" "ENSMUSG00000035448" "ENSMUSG00000036353"
 [76] "ENSMUSG00000036362" "ENSMUSG00000036381" "ENSMUSG00000036402"
 [79] "ENSMUSG00000036437" "ENSMUSG00000036832" "ENSMUSG00000037010"
 [82] "ENSMUSG00000037014" "ENSMUSG00000037140" "ENSMUSG00000037346"
 [85] "ENSMUSG00000037944" "ENSMUSG00000038607" "ENSMUSG00000038668"
 [88] "ENSMUSG00000038811" "ENSMUS

 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982019`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUSG00000019775" "ENSMUSG00000020599" "ENSMUSG00000021219"
 [7] "ENSMUSG00000024186" "ENSMUSG00000026357" "ENSMUSG00000026358"
[10] "ENSMUSG00000026475" "ENSMUSG00000026527" "ENSMUSG00000026678"
[13] "ENSMUSG00000028777" "ENSMUSG00000029101" "ENSMUSG00000032562"
[16] "ENSMUSG00000038530" "ENSMUSG00000042671" "ENSMUSG00000051079"
[19] "ENSMUSG00000052087" "ENSMUSG00000057614" "ENSMUSG00000059810"

$`R-MMU-8982020`
 [1] "ENSMUSG00000000001" "ENSMUSG00000002458" "ENSMUSG00000002459"
 [4] "ENSMUS

 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000024325" "ENSMUSG00000025577" "ENSMUSG00000025578"
 [7] "ENSMUSG00000026021" "ENSMUSG00000026484" "ENSMUSG00000026739"
[10] "ENSMUSG00000028796" "ENSMUSG00000037652" "ENSMUSG00000039989"
[13] "ENSMUSG00000040669"

$`R-MMU-4570463`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020265" "ENSMUSG00000020738" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000031347"
[13] "ENSMUSG00000037652" "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MMU-4570499`
 [1] "ENSMUSG00000000085" "ENSMUSG00000015120" "ENSMUSG00000018537"
 [4] "ENSMUSG00000020738" "ENSMUSG00000021546" "ENSMUSG00000024325"
 [7] "ENSMUSG00000025577" "ENSMUSG00000025578" "ENSMUSG00000026484"
[10] "ENSMUSG00000026739" "ENSMUSG00000028796" "ENSMUSG00000037652"
[13] "ENSMUSG00000039989" "ENSMUSG00000040669"

$`R-MM

 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-3781943`
 [1] "ENSMUSG00000000126" "ENSMUSG00000009900" "ENSMUSG00000010797"
 [4] "ENSMUSG00000012282" "ENSMUSG00000015957" "ENSMUSG00000018486"
 [7] "ENSMUSG00000021994" "ENSMUSG00000022382" "ENSMUSG00000022996"
[10] "ENSMUSG00000022997" "ENSMUSG00000026167" "ENSMUSG00000027840"
[13] "ENSMUSG00000028173" "ENSMUSG00000029671" "ENSMUSG00000030093"
[16] "ENSMUSG00000030170" "ENSMUSG00000033227" "ENSMUSG00000036856"
[19] "ENSMUSG00000036961"

$`R-MMU-205328`
[1] "ENSMUSG00000000127" "ENSMUSG00000005672" "ENSMUSG00000019966"
[4] "ENSMUSG00000032113" "ENSM

...

[1] "ENSMUSG00000036427"

$`R-MMU-6781899`
[1] "ENSMUSG00000036432" "ENSMUSG00000056900"

$`R-NUL-9620900`
[1] "ENSMUSG00000036478"

$`R-MMU-1679098`
[1] "ENSMUSG00000036499" "ENSMUSG00000045322"

$`R-MMU-187895`
[1] "ENSMUSG00000036499" "ENSMUSG00000045322"

$`R-MMU-1168635`
[1] "ENSMUSG00000036526" "ENSMUSG00000052889"

$`R-MMU-9605682`
[1] "ENSMUSG00000036587"

$`R-MMU-5692480`
[1] "ENSMUSG00000036622"

$`R-MMU-446214`
[1] "ENSMUSG00000036632"

$`R-MMU-2730959`
[1] "ENSMUSG00000036636" "ENSMUSG00000038280"

$`R-MMU-2395818`
[1] "ENSMUSG00000036639"

$`R-MMU-2395849`
[1] "ENSMUSG00000036639"

$`R-MMU-2395872`
[1] "ENSMUSG00000036639"

$`R-MMU-9731228`
[1] "ENSMUSG00000036639"

$`R-MMU-9731590`
[1] "ENSMUSG00000036639"

$`R-MMU-9731613`
[1] "ENSMUSG00000036639"

$`R-MMU-9731632`
[1] "ENSMUSG00000036639"

$`R-MMU-426520`
[1] "ENSMUSG00000036698"

$`R-MMU-5578712`
[1] "ENSMUSG00000036698" "ENSMUSG00000040029"

$`R-MMU-5578965`
[1] "ENSMUSG00000036698" "ENSMUSG00000052707"

$`R-MMU-55789

[1] "ENSMUSG00000037580" "ENSMUSG00000046814"

$`R-MMU-1474158`
[1] "ENSMUSG00000037580" "ENSMUSG00000046814"

$`R-MMU-1296037`
[1] "ENSMUSG00000037610" "ENSMUSG00000054934" "ENSMUSG00000091091"

$`R-MMU-6797627`
[1] "ENSMUSG00000037686"

$`R-MMU-6786650`
[1] "ENSMUSG00000037697" "ENSMUSG00000061313"

$`R-MMU-449734`
[1] "ENSMUSG00000037722"

$`R-MMU-391940`
[1] "ENSMUSG00000037759" "ENSMUSG00000039942"

$`R-MMU-428625`
[1] "ENSMUSG00000037771"

$`R-MMU-888592`
[1] "ENSMUSG00000037771"

$`R-MMU-5362564`
[1] "ENSMUSG00000037797" "ENSMUSG00000074207"

$`R-MMU-71707`
[1] "ENSMUSG00000037797" "ENSMUSG00000055301" "ENSMUSG00000074207"

$`R-MMU-174391`
[1] "ENSMUSG00000037798"

$`R-MMU-2408551`
[1] "ENSMUSG00000037798"

$`R-MMU-8869606`
[1] "ENSMUSG00000037847"

$`R-MMU-8869633`
[1] "ENSMUSG00000037847"

$`R-MMU-844619`
[1] "ENSMUSG00000037860"

$`R-MMU-877396`
[1] "ENSMUSG00000037860"

$`R-MMU-202703`
[1] "ENSMUSG00000037902" "ENSMUSG00000055447" "ENSMUSG00000074677"
[4] "ENSMUSG00000078780

[1] "ENSMUSG00000039760" "ENSMUSG00000074695"

$`R-MMU-71200`
[1] "ENSMUSG00000039783"

$`R-MMU-8854255`
[1] "ENSMUSG00000039813" "ENSMUSG00000079477"

$`R-MMU-442319`
[1] "ENSMUSG00000039878"

$`R-MMU-8875871`
[1] "ENSMUSG00000039908"

$`R-MMU-8879117`
[1] "ENSMUSG00000039952" "ENSMUSG00000066235"

$`R-MMU-9018768`
[1] "ENSMUSG00000039960"

$`R-MMU-9726862`
[1] "ENSMUSG00000039960"

$`R-MMU-391933`
[1] "ENSMUSG00000040016"

$`R-MMU-2995334`
[1] "ENSMUSG00000040018"

$`R-MMU-450494`
[1] "ENSMUSG00000040028"

$`R-MMU-450550`
[1] "ENSMUSG00000040028"

$`R-MMU-517674`
[1] "ENSMUSG00000040028"

$`R-MMU-517705`
[1] "ENSMUSG00000040028"

$`R-NUL-5362406`
[1] "ENSMUSG00000040035"

$`R-MMU-139909`
[1] "ENSMUSG00000040093"

$`R-MMU-8952137`
[1] "ENSMUSG00000040105"

$`R-MMU-9650858`
[1] "ENSMUSG00000040136" "ENSMUSG00000096146"

$`R-MMU-9652580`
[1] "ENSMUSG00000040136" "ENSMUSG00000096146"

$`R-MMU-141200`
[1] "ENSMUSG00000040147"

$`R-MMU-141202`
[1] "ENSMUSG00000040147"

$`R-MMU-9677929`
[1]

[1] "ENSMUSG00000042903" "ENSMUSG00000044167" "ENSMUSG00000048756"

$`R-MMU-9617657`
[1] "ENSMUSG00000042903"

$`R-MMU-9617711`
[1] "ENSMUSG00000042903"

$`R-MMU-9617755`
[1] "ENSMUSG00000042903"

$`R-NUL-9617710`
[1] "ENSMUSG00000042903"

$`R-NUL-9617742`
[1] "ENSMUSG00000042903"

$`R-NUL-9617757`
[1] "ENSMUSG00000042903"

$`R-NUL-9617903`
[1] "ENSMUSG00000042903"

$`R-NUL-9617912`
[1] "ENSMUSG00000042903"

$`R-MMU-187246`
[1] "ENSMUSG00000043013" "ENSMUSG00000045518"

$`R-MMU-189119`
[1] "ENSMUSG00000043013" "ENSMUSG00000045518"

$`R-MMU-391942`
[1] "ENSMUSG00000043017"

$`R-MMU-9726949`
[1] "ENSMUSG00000043017"

$`R-MMU-1564169`
[1] "ENSMUSG00000043089" "ENSMUSG00000056174" "ENSMUSG00000068196"

$`R-MMU-1602473`
[1] "ENSMUSG00000043089"

$`R-MMU-389424`
[1] "ENSMUSG00000043102"

$`R-MMU-9014672`
[1] "ENSMUSG00000043241" "ENSMUSG00000058301"

$`R-MMU-9014678`
[1] "ENSMUSG00000043241" "ENSMUSG00000058301"

$`R-MMU-162873`
[1] "ENSMUSG00000043257"

$`R-MMU-8878914`
[1] "ENSMUSG00000043

[4] "ENSMUSG00000070719" "ENSMUSG00000098488"

$`R-MMU-1482897`
[1] "ENSMUSG00000046971" "ENSMUSG00000056220" "ENSMUSG00000070719"

$`R-MMU-1482920`
[1] "ENSMUSG00000046971" "ENSMUSG00000070719"

$`R-MMU-9794031`
[1] "ENSMUSG00000047002"

$`R-MMU-437240`
[1] "ENSMUSG00000047139"

$`R-MMU-140355`
[1] "ENSMUSG00000047250"

$`R-MMU-140359`
[1] "ENSMUSG00000047250"

$`R-MMU-2314678`
[1] "ENSMUSG00000047250"

$`R-MMU-9677320`
[1] "ENSMUSG00000047250"

$`R-MMU-6803890`
[1] "ENSMUSG00000047281"

$`R-MMU-947531`
[1] "ENSMUSG00000047454"

$`R-MMU-5340195`
[1] "ENSMUSG00000047638"

$`R-MMU-6806674`
[1] "ENSMUSG00000047719"

$`R-MMU-190681`
[1] "ENSMUSG00000047797"

$`R-MMU-9846477`
[1] "ENSMUSG00000047878"

$`R-MMU-8850846`
[1] "ENSMUSG00000048120"

$`R-MMU-8850854`
[1] "ENSMUSG00000048120"

$`R-MMU-8954468`
[1] "ENSMUSG00000048142"

$`R-MMU-70542`
[1] "ENSMUSG00000048217"

$`R-MMU-6804402`
[1] "ENSMUSG00000048349" "ENSMUSG00000059552"

$`R-MMU-418172`
[1] "ENSMUSG00000048376" "ENSMUSG0000006021

In [39]:
%%R
rxns <- rxn2ensembls.nls %>% names()
print(length(rxns))
print(rxns)

In [40]:
%%R
rxn_knn_misclass_rate.nls <- list()
rxn_knn_ari.nls <- list()
rxn_knn_ecount.nls <- list()
rxn_pca.nls <- list()
count <- 0

In [41]:
%%R
toi_indices <- seq(1,length(tcdd_dose_detail.vec))
print(toi_indices)

In [42]:
%%R
tcdd_dose_detail_vec_tis_of_interest <-
   tcdd_dose_detail.vec[toi_indices]
print(tcdd_dose_detail_vec_tis_of_interest)

In [43]:
%%R
vst.count.mtx.tis_of_interest <- vst.count.mtx[, toi_indices]
print(vst.count.mtx.tis_of_interest)

   9.021620   8.341945
ENSMUSG00000000532  11.332315  11.705518  11.733846  11.524644  12.735737
ENSMUSG00000000552  12.012008  11.346182  12.289990  12.195326   9.429317
ENSMUSG00000000555  14.036980  13.178566  14.365655  13.457641  10.898582
ENSMUSG00000000560   5.464603   5.464509   5.452182   5.479097   5.478940
ENSMUSG00000000561  13.273549  13.084141  13.192699  12.950261  12.968167
ENSMUSG00000000562   5.464603   5.464509   6.377416   5.479097   5.478940
ENSMUSG00000000563  17.005217  17.036854  16.554615  17.054706  17.243609
ENSMUSG00000000567   9.320471   8.384323   9.670719   8.987120   8.246228
ENSMUSG00000000568  13.781964  13.951526  13.833196  13.735974  15.142163
ENSMUSG00000000579   6.576615   7.117824   7.165282   5.479097   7.761689
ENSMUSG00000000581  14.098701  14.529676  13.629333  13.885629  15.319122
ENSMUSG00000000594  15.807537  16.171212  15.127519  15.746123  16.164951
ENSMUSG00000000605  15.184152  14.819876  14.701499  14.742217  15.190068
ENSMUSG00000000

ENSMUSG00000010095  14.127672  13.508110  13.480341  13.716120  13.377694
ENSMUSG00000010097  15.123122  14.982669  15.037432  14.812224  14.112976
ENSMUSG00000010110  14.283646  15.119238  14.594066  14.143209  14.271426
ENSMUSG00000010122  16.623364  15.503518  15.703171  16.208955  16.774372
ENSMUSG00000010142   6.632340   5.464509   7.041573   6.239489   6.721127
ENSMUSG00000010311   5.464603   5.464509   5.452182   5.479097   5.478940
ENSMUSG00000010376  13.832454  13.968276  14.325788  14.467647  13.383797
ENSMUSG00000010392  13.712644  13.767306  13.173492  13.684418  14.127914
ENSMUSG00000010406  12.348005  13.402080  12.429784  12.951023  11.818265
ENSMUSG00000010453  14.311621  14.425810  14.319030  14.970292  14.374257
ENSMUSG00000010461   6.922094   6.786572   6.555632   5.479097   6.888145
ENSMUSG00000010601  16.496116  15.966313  16.155226  15.941113  16.737166
ENSMUSG00000010607  11.189059  11.978690  11.087762  12.646163   9.902426
ENSMUSG00000010608  16.055457  15.2480

ENSMUSG00000014867  17.683677  17.694123  17.911207  17.761132  16.943323
ENSMUSG00000014932  12.827349  12.655485  12.180109  12.500208  14.139154
ENSMUSG00000014956  16.070287  15.890472  15.743849  15.947718  16.951471
ENSMUSG00000014959  15.626149  16.072491  15.799212  15.610865  14.995214
ENSMUSG00000015013   8.855627  10.140746  10.036552   9.493306  10.771058
ENSMUSG00000015016  12.980108  13.419276  12.499132  13.394867  12.452367
ENSMUSG00000015027   9.658167  10.160669  10.721301   9.860236   9.611674
ENSMUSG00000015053   7.348616   7.598807   7.224687   7.761802   6.797826
ENSMUSG00000015083  17.623057  17.981602  17.239863  18.009618  17.415799
ENSMUSG00000015085   7.816541   9.459881   8.999259   9.091803   8.210267
ENSMUSG00000015090   9.851447  10.092500   9.058955   8.809657   8.319967
ENSMUSG00000015094   8.478197   9.673197   9.616489   9.296642   8.253850
ENSMUSG00000015095  13.534482  13.288089  13.441737  13.497504  12.341065
ENSMUSG00000015112  17.254359  16.7877

ENSMUSG00000016496   8.126796   8.108270   9.930421   8.201960   8.678545
ENSMUSG00000016498   5.464603   5.464509   5.452182   5.479097   6.238846
ENSMUSG00000016503  12.369053  12.227858  12.386509  12.032969  11.546148
ENSMUSG00000016524   5.464603   5.464509   5.452182   5.479097   5.478940
ENSMUSG00000016528  14.312550  14.697382  14.334311  14.510975  13.507082
ENSMUSG00000016529   6.443172   5.464509   6.128454   5.479097   5.478940
ENSMUSG00000016534  19.100458  19.049970  18.662459  18.915590  19.317149
ENSMUSG00000016554  15.001133  15.186908  14.866457  14.711572  14.508993
ENSMUSG00000016559  16.012897  15.952315  15.791244  15.589238  16.869732
ENSMUSG00000016619  13.797664  13.081872  13.238486  12.857973  13.660460
ENSMUSG00000016637   9.884001  10.276642  10.786723  10.150963  10.324201
ENSMUSG00000016664  14.898036  14.948279  14.223390  14.547428  14.444490
ENSMUSG00000016757  11.247507  10.299230  11.012862  11.401030   9.620880
ENSMUSG00000016763   6.179851   6.7865

ENSMUSG00000018347   8.576083   9.218391   8.936017   8.984375   9.137602
ENSMUSG00000018362  10.124779  10.206728  10.201339   9.823203   9.320219
ENSMUSG00000018363  14.382554  14.400310  14.521151  14.582085  14.374354
ENSMUSG00000018379  16.495644  16.056302  16.119093  16.209891  16.820845
ENSMUSG00000018395   8.127939   9.007794   8.101746   8.787872   8.613054
ENSMUSG00000018401  15.516091  15.153727  14.986620  14.583919  14.058342
ENSMUSG00000018411   8.994948   8.399339   8.660027   8.816546   9.288958
ENSMUSG00000018412  13.180756  12.219154  12.702647  12.705341  13.076770
ENSMUSG00000018428  16.083604  15.896701  15.821244  15.900650  15.809868
ENSMUSG00000018433  11.519140  11.093557  11.484520  11.447339  11.528926
ENSMUSG00000018442  16.181737  15.774197  15.053904  15.702670  16.067158
ENSMUSG00000018446  15.211372  14.618197  14.745889  15.331616  14.373095
ENSMUSG00000018459  11.533185  10.931940  13.496812  11.244810  11.491384
ENSMUSG00000018470   7.437138   6.6809

...

ENSMUSG00000015095  14.843027  14.315272  15.126667  15.157011  15.095541
ENSMUSG00000015112  15.906298  14.821022  14.543247  14.579609  14.678821
ENSMUSG00000015120  12.031182  12.687911  10.334774  12.559673   9.843476
ENSMUSG00000015127  12.037119  10.871521  10.940302  11.003391  10.829940
ENSMUSG00000015134   6.670895   7.346042   6.860215   7.023591   6.484898
ENSMUSG00000015143  14.735279  12.951217  13.455198  12.925434  13.696124
ENSMUSG00000015149  13.893008  13.370780  14.077132  14.341674  14.194098
ENSMUSG00000015165  14.699638  14.938370  15.338081  15.023840  15.454694
ENSMUSG00000015214  13.691509  13.451379  11.534656  13.300026  11.714641
ENSMUSG00000015243  16.067023  16.863947  13.312217  16.370440  13.363931
ENSMUSG00000015291  15.280366  14.071094  14.519650  14.958186  14.362112
ENSMUSG00000015314   6.911758   7.319682   7.411726   7.655930   6.925900
ENSMUSG00000015340  13.777423  14.253028  13.020461  14.164523  13.037746
ENSMUSG00000015341  14.155144  13.9953

ENSMUSG00000016757  12.411899  11.266474  11.757094  11.428741  11.932962
ENSMUSG00000016763   7.391974   8.029473   7.709405   7.869200   7.649838
ENSMUSG00000016833  10.975817  11.641162  13.166578  10.472773  13.000610
ENSMUSG00000016933  14.954024  14.591926  13.265334  14.747036  13.323653
ENSMUSG00000016942  17.129235  16.500219  17.733403  16.474618  17.611853
ENSMUSG00000016995   5.431819   6.061860   5.442724   5.980577   6.084952
ENSMUSG00000017002   9.846662  12.210568  11.049785   9.434381  10.897207
ENSMUSG00000017009  15.228836  16.704106  16.382390  16.152401  16.455203
ENSMUSG00000017057  12.498425  12.005519  12.064366  12.227723  11.971273
ENSMUSG00000017119  16.966997  16.702202  16.136831  16.718258  16.253858
ENSMUSG00000017132  12.418173  12.648859  11.836745  12.910491  12.197082
ENSMUSG00000017144  11.242877  11.785896   9.932451  11.179152  10.131923
ENSMUSG00000017146   9.842759   8.838151   8.464016   8.582491   8.191334
ENSMUSG00000017165   5.431819   5.3938

ENSMUSG00000018459  16.449472  16.625679  16.074643  17.488412  16.012710
ENSMUSG00000018470   6.670895   6.699490   5.442724   6.834857   6.469614
ENSMUSG00000018474  15.416788  15.217989  13.717357  15.111561  13.776274
ENSMUSG00000018476  11.650380  11.905190   9.893396  12.135492  10.119852
ENSMUSG00000018486   8.231827   8.773768   8.058689   9.266486   8.253760
ENSMUSG00000018500   6.420977   6.529247   7.097889   6.938870   6.627988
ENSMUSG00000018507   9.654191  10.175307   9.603847  10.682557  10.035636
ENSMUSG00000018537   9.019720   8.341801   9.621950   9.473184   9.953683
ENSMUSG00000018541  10.406697  10.703944   9.812630  10.836755   9.887964
ENSMUSG00000018547  11.916593  11.882278  10.830547  10.937121  10.842755
ENSMUSG00000018548  12.532910  12.138228  11.215114  12.365934  11.523601
ENSMUSG00000018559  12.374576  12.033083  14.453382  12.304861  14.462186
ENSMUSG00000018566   6.268679   6.377004   6.494163   6.646062   6.321681
ENSMUSG00000018567  16.117062  16.2795

ENSMUSG00000019761   7.181842   7.293481   8.506043   7.458875   8.706876
ENSMUSG00000019762  14.974097  13.668156  14.453382  12.306491  14.502903
ENSMUSG00000019768  10.525976  10.950125  10.248113  10.886192  10.336115
ENSMUSG00000019772   5.431819   5.393895   5.442724   5.416669   5.441712
ENSMUSG00000019773   8.199258   7.871123   7.662962   7.972499   7.996497
ENSMUSG00000019774   8.480238   8.509748   9.295545   8.475395   8.936628
ENSMUSG00000019775   6.268679   6.810784   6.089163   6.451982   5.441712
ENSMUSG00000019779   8.638945   9.703386   8.308462   8.690116   8.042449
ENSMUSG00000019782   9.843824   9.597063  11.589936   9.554107  11.514395
ENSMUSG00000019785   5.431819   6.190319   5.442724   5.416669   5.441712
ENSMUSG00000019787   5.431819   5.393895   5.442724   5.416669   5.441712
ENSMUSG00000019789   6.268679   6.190319   6.323182   6.801815   6.084952
ENSMUSG00000019795  12.430933  12.385209  13.024808  12.577810  13.207987
ENSMUSG00000019803   5.431819   5.3938

ENSMUSG00000000826  15.112981  15.038539  15.182657  14.880096  14.956933
ENSMUSG00000000869   6.411032   6.220177   5.643167   6.224714   6.840623
ENSMUSG00000000876  14.073991  15.634131  14.180697  14.401308  14.133756
ENSMUSG00000000881  11.346063  11.285116  11.641881  12.131982  10.603321
ENSMUSG00000000889   5.969189   5.443557   5.426896   5.433797   5.442831
ENSMUSG00000000901  13.467257  13.142932  13.562095  12.435932  14.762215
ENSMUSG00000000902  11.276927  11.158533  11.263606  11.155698  11.662054
ENSMUSG00000000903   5.969189   6.327606   6.525299   5.433797   5.442831
ENSMUSG00000000915  12.875740  12.639517  12.836137  13.060763  12.895050
ENSMUSG00000000942   7.507652   6.373060   6.629476   7.373594   7.174762
ENSMUSG00000000957  13.428821  14.685265  12.881604  12.570016  14.035165
ENSMUSG00000000958  10.043668   8.965332   9.215440   9.360339   9.940253
ENSMUSG00000000959  13.902299  13.276926  13.694098  13.753001  14.377960
ENSMUSG00000000982   8.240379   7.5544

In [44]:
%%R
training_indices <-
   caret::createDataPartition(
      tcdd_dose_detail_vec_tis_of_interest,
      times = 1,
      p = 1.0, # no data will be held out when set to "1.0"
      list = FALSE
   )
print(training_indices)

In [45]:
%%R
vst.count.mtx.train <-
   vst.count.mtx.tis_of_interest[, training_indices] #9/10ths of data
vst.count.mtx.test  <-
   vst.count.mtx.tis_of_interest[, -training_indices] #1/10th of data

print(vst.count.mtx.train)

  11.664783
ENSMUSG00000002346  15.913715  16.241498  15.072689  15.361091  16.014483
ENSMUSG00000002365  14.138497  14.449142  14.628842  14.095083  14.057259
ENSMUSG00000002379  13.523638  14.190660  13.282098  13.170529  14.297317
ENSMUSG00000002393  15.557099  15.943931  13.758405  12.938298  16.555272
ENSMUSG00000002395  13.544400  13.755923  12.909420  13.193661  13.651159
ENSMUSG00000002413  12.769701  12.776269  13.320475  13.062252  12.725294
ENSMUSG00000002416  13.309748  14.080104  13.680980  13.338193  14.009736
ENSMUSG00000002428  10.918846  11.273933  11.797763  11.271570  11.109789
ENSMUSG00000002455  14.249760  15.296190  14.096553  13.966310  15.305357
ENSMUSG00000002458   7.473843   6.540605   7.945466   6.522123   6.855439
ENSMUSG00000002459   5.468450   6.118357   5.476903   5.479580   5.455976
ENSMUSG00000002475  15.057413  14.965493  14.934834  14.916555  14.971066
ENSMUSG00000002477   9.262847   9.422992  10.795247  10.907010  10.092356
ENSMUSG00000002496  14.469

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



  12.836433  12.844516  12.146963  12.103372  12.135350
ENSMUSG00000004455  11.268793  11.489818  11.817655  12.341739  10.612567
ENSMUSG00000004500   9.259237   9.378123   9.303382   8.560683   9.277636
ENSMUSG00000004535  16.638386  16.359271  16.701841  16.756789  16.314465
ENSMUSG00000004552   6.656120   6.118357   5.476903   5.479580   6.144179
ENSMUSG00000004565  13.265802  13.386986  13.015612  12.695959  14.414063
ENSMUSG00000004567  14.521620  14.713099  13.534032  13.479584  13.853542
ENSMUSG00000004568  12.805280  12.430024  12.698093  12.470072  13.400336
ENSMUSG00000004591  14.138208  14.095046  14.505431  14.593641  14.261933
ENSMUSG00000004609   7.535763   7.350398   7.565843   7.287729   6.397537
ENSMUSG00000004610  17.221537  17.515080  17.495359  17.577028  17.435611
ENSMUSG00000004626  13.507117  13.806492  13.152941  13.055684  13.507147
ENSMUSG00000004630   6.432107   7.444084   7.536365   7.169090   7.087500
ENSMUSG00000004633  14.653956  14.476096  14.080200  14.

ENSMUSG00000005580  11.809831  12.052457  11.918829  12.279551  11.726502
ENSMUSG00000005583   8.693659   7.911061   8.780132   8.874040   8.563873
ENSMUSG00000005609  13.105621  13.030136  12.490390  12.336781  13.522664
ENSMUSG00000005610  18.782735  18.686351  18.653716  18.515269  18.739969
ENSMUSG00000005611   6.951931   7.353420   8.227436   7.276320   7.771135
ENSMUSG00000005615  16.345518  16.286284  16.080405  16.004907  15.779783
ENSMUSG00000005625  15.622116  15.774505  15.209928  15.326655  15.995177
ENSMUSG00000005628   7.242168   6.918589   6.508025   6.522123   5.825433
ENSMUSG00000005667   7.468567   6.962179   6.823568   6.503481   9.027839
ENSMUSG00000005672   8.895224   9.211193   9.337621   9.870680   9.506201
ENSMUSG00000005677  18.584783  18.237219  18.477115  19.184701  17.163220
ENSMUSG00000005681  21.471786  21.852660  21.616042  21.746380  21.670532
ENSMUSG00000005682  13.914556  13.854546  13.790656  13.743395  13.923041
ENSMUSG00000005683  16.128773  16.1930

ENSMUSG00000006728  16.595163  16.346111  15.456583  15.608481  16.256093
ENSMUSG00000006731  14.777568  15.228844  14.626011  14.422724  15.166272
ENSMUSG00000006740  14.501610  13.700702  14.422927  14.580931  13.786343
ENSMUSG00000006764   5.468450   5.449749   5.476903   5.479580   5.455976
ENSMUSG00000006777   8.599257   7.536215   8.615723   8.843957   7.347095
ENSMUSG00000006818  17.152022  17.497828  17.303271  17.315442  17.405487
ENSMUSG00000006906  11.622536  10.779373  11.949900  11.869223  11.212416
ENSMUSG00000006932  17.107180  17.239185  17.216563  16.884586  17.372589
ENSMUSG00000006998  16.324368  16.426023  16.421537  16.165099  16.580855
ENSMUSG00000007033   9.295817   8.935367   8.226180   7.924446  10.764764
ENSMUSG00000007034   5.468450   6.656934   7.017731   6.444516   5.684810
ENSMUSG00000007038  13.794711  14.145318  13.223402  13.428088  13.848500
ENSMUSG00000007050  11.054533  11.645120  10.709511  10.020020  11.655493
ENSMUSG00000007080   7.720135   8.5386

...

ENSMUSG00000000776  11.715729  10.798229  10.608129  11.643816  10.063109
ENSMUSG00000000782   8.504798   8.678327   8.914907   8.952376   9.293000
ENSMUSG00000000787  17.041871  16.870635  17.556668  17.609104  17.299927
ENSMUSG00000000791   8.037375   8.129516   7.156214   7.170512   7.595357
ENSMUSG00000000792   6.086012   6.069486   5.426183   5.439281   5.427087
ENSMUSG00000000794   6.086012   6.602249   6.238317   6.611140   6.819070
ENSMUSG00000000805   5.441967   5.437998   5.426183   5.439281   5.427087
ENSMUSG00000000817   6.489488   6.819124   6.506358   6.475869   6.400124
ENSMUSG00000000823  14.638168  13.915998  13.784265  14.075195  14.808577
ENSMUSG00000000826  15.270809  15.000638  14.966961  15.275348  14.959373
ENSMUSG00000000869   6.406367   6.298010   6.114360   5.439281   6.080982
ENSMUSG00000000876  15.391891  14.414952  14.388411  14.109296  15.668625
ENSMUSG00000000881  11.026458  10.974482  10.706827  11.238354  10.806193
ENSMUSG00000000889   5.441967   5.4379

ENSMUSG00000001918  13.274206  14.044847  13.716317  14.630895  14.688351
ENSMUSG00000001924  16.702421  16.819536  16.708433  16.865740  16.527447
ENSMUSG00000001930  12.537129  11.228687  12.080463  11.342190  10.902551
ENSMUSG00000001946  12.735962  11.541485  11.813868  10.317799  10.901007
ENSMUSG00000001962  11.386462  11.526521  11.450546  12.365395  11.306146
ENSMUSG00000001964  11.772598  11.735767  11.583708  11.079146  11.520329
ENSMUSG00000001983  11.167811  11.703414  11.604527  12.085662  11.057288
ENSMUSG00000001985   5.441967   5.437998   6.020233   5.439281   6.024005
ENSMUSG00000001986   7.345335   7.155744   6.723903   7.869821   6.634992
ENSMUSG00000001998  10.427871  10.133861  11.481010  10.644803  11.241929
ENSMUSG00000001999  11.328828  11.717572  11.341551  11.287964  11.220750
ENSMUSG00000002010  15.395361  15.120678  14.892554  14.339477  13.034617
ENSMUSG00000002015  16.324323  16.611902  16.338333  16.402374  17.018045
ENSMUSG00000002020   9.694821   9.3110

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



  14.114007  14.106997  13.670620  14.417218
ENSMUSG00000004630   6.748080   7.119530   7.017218   6.349360   6.784840
ENSMUSG00000004633   8.749609   9.895633   9.157026  11.034839  10.822389
ENSMUSG00000004637  11.768703  11.677350  11.223531  11.138350  11.146336
ENSMUSG00000004642  11.616943  11.117790  11.050612  12.044378  10.732867
ENSMUSG00000004651   5.441967   5.437998   5.426183   5.439281   5.427087
ENSMUSG00000004654   6.086012   5.437998   5.426183   5.439281   6.024005
ENSMUSG00000004655  17.291116  16.861015  17.323564  15.325238  16.042694
ENSMUSG00000004665  12.179206  11.377924  11.928483  10.719966  10.051521
ENSMUSG00000004667  12.827054  13.045833  11.853151  12.252112  11.666871
ENSMUSG00000004668   6.266180   5.437998   5.426183   6.074830   6.365931
ENSMUSG00000004677  14.435432  13.935719  13.394522  13.719679  13.124675
ENSMUSG00000004709   7.955907   8.032602   7.273778   7.312525   7.986778
ENSMUSG00000004730  12.819185  12.274042  13.709703  13.148425  11.

ENSMUSG00000005682  14.802252  14.335416  14.734192  13.715451  14.305442
ENSMUSG00000005683  16.412230  16.514687  16.451045  15.578222  15.820453
ENSMUSG00000005686   9.712544   8.845843   9.369050   8.013468   8.926543
ENSMUSG00000005687  12.747005  13.200502  12.584253  13.358115  12.835910
ENSMUSG00000005698  13.056726  13.049099  13.143518  13.438240  13.326965
ENSMUSG00000005699   8.615685   8.771684   8.579802   7.695629   7.796040
ENSMUSG00000005705   6.330741   6.599775   6.238317   6.727615   5.926154
ENSMUSG00000005716   5.441967   5.437998   5.426183   5.439281   5.427087
ENSMUSG00000005763   9.270343   8.673340   8.580351   8.216401   9.522862
ENSMUSG00000005779  16.248776  16.453219  16.291378  16.231484  15.766634
ENSMUSG00000005800  14.306465  12.761001  13.764672  13.037226  12.682793
ENSMUSG00000005803  15.344339  16.213287  15.645069  15.368421  15.162687
ENSMUSG00000005804  11.050515  11.492429  11.602038  11.444362  11.080661
ENSMUSG00000005813  14.321092  14.0778

In [46]:
%%R
tcdd_dose_detail.vec.train <-
   tcdd_dose_detail_vec_tis_of_interest[training_indices]
tcdd_dose_detail.vec.test <-
   tcdd_dose_detail_vec_tis_of_interest[-training_indices]

# print(gtex_tissue_detail.vec.train)
print(length(unique(tcdd_dose_detail.vec.train)))

In [47]:
%%R
saveRDS(tcdd_dose_detail.vec.train,file=paste(OUT_DIR,"tcdd_dose_detail_vec_train030_time_cross_60.Rds",sep=""))

In [48]:
%%R
cv_fold_indices <- caret::createFolds(tcdd_dose_detail.vec.train,
                                      k = N_FOLDS)
print(cv_fold_indices)

In [49]:
%%R
binary_tcdd_dose_annotations <- unique(tcdd_dose_detail.vec)
print(binary_tcdd_dose_annotations)

In [50]:
%%R
full_rxn_pca_results.nls <- list()
rxn_id_2_result_file_idx.nls <- list()

In [51]:
%%R
n_rxns <- length(rxns)
print(n_rxns)
result_idx <- 1
for(rxn_id_idx in seq(1:n_rxns)){
   rxn_id <- rxns[rxn_id_idx]
   rxn_pca <-
      prcomp(t(vst.count.mtx.train[rxn2ensembls.nls[[rxn_id]], ]), scale. = T)
   full_rxn_pca_results.nls[[rxn_id]] <- rxn_pca
   rxn_id_2_result_file_idx.nls[[rxn_id]] <- result_idx
   rxn_pca.nls[[rxn_id]] <-
      rxn_pca$x[, 1] # 1st principal component coordinate within this reaction-space for each sample
   if(mod(rxn_id_idx,100) == 0){
      print(paste("Processed ",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      flush.console()
   }
   if(mod(rxn_id_idx,1000) == 0){
      print(paste("Storing PCA objects containing reactions ",rxn_id_idx-1000,
                  "-",rxn_id_idx,
                  " of ",n_rxns,
                  " reactions (",round((rxn_id_idx + 1)/n_rxns,digits = 3) * 100,"%)...",
                  sep=""))
      saveRDS(full_rxn_pca_results.nls,
              paste(OUT_DIR, "full_rxn_pca_results_nls",rxn_id_idx-1000,
                    "-",rxn_id_idx,"030_time_cross_60.Rds", sep=""))
      full_rxn_pca_results.nls <- list()
      gc()
      result_idx <- result_idx + 1
   }
}

[1] "Processed 4100 of 9825 reactions (41.7%)..."
[1] "Processed 4200 of 9825 reactions (42.8%)..."
[1] "Processed 4300 of 9825 reactions (43.8%)..."
[1] "Processed 4400 of 9825 reactions (44.8%)..."
[1] "Processed 4500 of 9825 reactions (45.8%)..."
[1] "Processed 4600 of 9825 reactions (46.8%)..."
[1] "Processed 4700 of 9825 reactions (47.8%)..."
[1]

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [52]:
%%R
# store remaining PCA objects and removing from RAM
saveRDS(rxn_id_2_result_file_idx.nls,
        paste(OUT_DIR,"rxn_id_2_result_file_idx_nls030_time_cross_60.Rds",sep=""))
saveRDS(full_rxn_pca_results.nls,
        paste(OUT_DIR, "full_rxn_pca_results_nls030_time_cross_60.Rds", sep=""))
rm(full_rxn_pca_results.nls)
gc()

           used  (Mb) gc trigger  (Mb) max used  (Mb)
Ncells  7240325 386.7   13077572 698.5 13077572 698.5
Vcells 17784125 135.7   31091163 237.3 31091151 237.3


In [ ]:
%%R
print(rxn_pca.nls)

$`R-MMU-170666`
SRR7817659 SRR7817662 SRR1636592 SRR1636589 SRR7817700 SRR7817675 SRR7817695 
-2.3025400 -3.0018530 -2.8096385 -3.7895556 -2.0991053 -1.0600862 -2.0695276 
SRR7817699 SRR3593527 SRR7817616 SRR7817686 SRR7817626 SRR7817671 SRR7817696 
-1.6906225 -1.7242214 -1.9543301 -2.2379832 -2.6562601 -0.9231897 -1.6511309 
SRR1636588 SRR7817652 SRR1636593 SRR7817674 SRR4317609 SRR7817663 SRR7817661 
-3.7962726 -3.8167936 -2.2896588 -2.1170354 -2.8078299 -3.5774286 -3.3379334 
SRR7817685 SRR1636586 SRR4317611 SRR3593525 SRR7817676 SRR7817684 SRR7817614 
-1.4929645 -2.0027188 -2.0559763 -2.1032943 -1.7657255 -3.3917346 -2.3172041 
SRR7817623 SRR7817612 SRR7817698 SRR7817638 SRR7817647 SRR7817649 SRR7817664 
-1.6472525 -0.8904309 -2.2888883 -2.6129660 -3.5943505 -2.5715289 -3.1556469 
SRR7817672 SRR7817628 SRR1636591 SRR7817651 SRR1636590 SRR7817641 SRR4317658 
-0.8924921 -2.9770336 -3.2155527 -3.6388296 -3.1667595  3.2664829  1.7187466 
SRR7817693 SRR4317657 SRR7817680 SRR7817658 SRR7

  7.6816608   7.7707107  10.4124979   7.8027067 -10.2591836  -5.8141851 
 SRR7817693  SRR4317657  SRR7817680  SRR7817658  SRR7817645  SRR1636673 
 -7.8277923  -6.0792010  -4.0646996  -7.2375528  -9.4015910  -0.4985579 
 SRR7817633  SRR1636676  SRR7817705  SRR4317655  SRR7817617  SRR7817701 
 -8.2106947  -0.2212246  -5.7199845 -11.0956823  -7.2549959 -12.0443076 
 SRR7817618  SRR7817666  SRR3593578  SRR7817678  SRR7817682  SRR7817670 
 -7.3030975 -11.4910972  -4.7834296  -8.9237918  -7.9641683  -7.5092130 
 SRR7817706  SRR7817630  SRR7817634  SRR7817621  SRR7817631  SRR7817692 
 -5.7448198  -8.5461866  -8.7379612 -12.7106979 -13.4243228  -8.0585724 
 SRR7817694  SRR7817632  SRR1636674  SRR7817665  SRR4317656  SRR7817702 
 -7.4528801 -13.3143713  -0.6507242 -11.2350496 -10.7849273 -12.2051627 
 SRR7817689  SRR1636671  SRR7817656  SRR7817646  SRR7817668  SRR7817703 
-11.3487669   1.7873459  -9.0327779  -9.4291640  -7.1061675  -8.4685558 
 SRR7817679  SRR3593580 
 -3.5779000  -5.2888626 



 SRR7817689  SRR1636671  SRR7817656  SRR7817646  SRR7817668  SRR7817703 
-11.2559988   1.6817889  -8.8181967  -9.2024387  -7.0882651  -8.4171544 
 SRR7817679  SRR3593580 
 -3.7137744  -5.2404490 

$`R-MMU-749456`
 SRR7817659  SRR7817662  SRR1636592  SRR1636589  SRR7817700  SRR7817675 
  8.2291907   8.0905309   8.9504455   8.4052164   8.1937129   6.5450860 
 SRR7817695  SRR7817699  SRR3593527  SRR7817616  SRR7817686  SRR7817626 
  8.6255372   8.4766518   4.8950148   6.1707564   8.6579701   8.3370932 
 SRR7817671  SRR7817696  SRR1636588  SRR7817652  SRR1636593  SRR7817674 
  4.0149076   8.6959418   9.0035309   9.5141535   8.0244633   6.1611818 
 SRR4317609  SRR7817663  SRR7817661  SRR7817685  SRR1636586  SRR4317611 
  6.4219390   9.0782836   8.4436753   8.1768201   8.8591086   4.0836114 
 SRR3593525  SRR7817676  SRR7817684  SRR7817614  SRR7817623  SRR7817612 
  6.2077983   6.1683477   9.3787528   6.6639574   6.4770671   5.0776212 
 SRR7817698  SRR7817638  SRR7817647  SRR7817649  SRR78176

-2.1037159 -1.9058634 -1.4345334 -1.7701510 -2.3888549 -1.8332755 -2.0081630 
SRR7817685 SRR1636586 SRR4317611 SRR3593525 SRR7817676 SRR7817684 SRR7817614 
-1.7967213 -1.3985989 -1.9719749 -1.5019663 -1.3547286 -2.0836670 -1.6228902 
SRR7817623 SRR7817612 SRR7817698 SRR7817638 SRR7817647 SRR7817649 SRR7817664 
-1.8103298 -1.2894688 -2.0706927 -1.3869198 -1.7522790 -1.7872020 -1.7344520 
SRR7817672 SRR7817628 SRR1636591 SRR7817651 SRR1636590 SRR7817641 SRR4317658 
-1.1226806 -1.6319599 -2.1004472 -1.8432274 -1.7202721  2.5098516  0.9111220 
SRR7817693 SRR4317657 SRR7817680 SRR7817658 SRR7817645 SRR1636673 SRR7817633 
 1.7441569  0.7593123  0.8326421  1.9497651  2.6254119 -0.3712293  1.2005821 
SRR1636676 SRR7817705 SRR4317655 SRR7817617 SRR7817701 SRR7817618 SRR7817666 
-0.1646785  1.6770383  1.9438346  0.3696445  2.8973378  1.0161324  3.0704637 
SRR3593578 SRR7817678 SRR7817682 SRR7817670 SRR7817706 SRR7817630 SRR7817634 
 0.8506218  2.3804983  1.9960448  1.7540280  1.8994035  1.658498

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



...

 SRR7817631  SRR7817692 
-1.86652916 -2.14451402 -2.73399029 -3.46206836 -3.12286435 -2.14940273 
 SRR7817694  SRR7817632  SRR1636674  SRR7817665  SRR4317656  SRR7817702 
-2.73971809 -3.50474488  0.63942231 -1.97933644 -1.53995601 -2.42618271 
 SRR7817689  SRR1636671  SRR7817656  SRR7817646  SRR7817668  SRR7817703 
-2.81122012  1.33067659 -2.29875555 -3.05737772 -2.25994558 -1.62972738 
 SRR7817679  SRR3593580 
-0.51455503 -0.70223026 

$`R-MMU-9018745`
SRR7817659 SRR7817662 SRR1636592 SRR1636589 SRR7817700 SRR7817675 SRR7817695 
 2.0528857  3.1291790  2.5945019  3.2072387  3.0053551  1.9867886  3.4710353 
SRR7817699 SRR3593527 SRR7817616 SRR7817686 SRR7817626 SRR7817671 SRR7817696 
 2.3028017  1.1244909  2.1383386  3.5916333  2.0082309  0.7842724  3.2237826 
SRR1636588 SRR7817652 SRR1636593 SRR7817674 SRR4317609 SRR7817663 SRR7817661 
 3.6510636  4.0255975  3.0374356  1.1457056  1.9101424  2.3649467  2.6767888 
SRR7817685 SRR1636586 SRR4317611 SRR3593525 SRR7817676 SRR7817684 SRR78176

-0.181116200 -0.195550544 -0.838567652  0.921459625  0.002936842  1.018700408 
  SRR7817694   SRR7817632   SRR1636674   SRR7817665   SRR4317656   SRR7817702 
 0.636588085  0.244658810 -1.914203485 -0.152303889  0.131824714  1.227539093 
  SRR7817689   SRR1636671   SRR7817656   SRR7817646   SRR7817668   SRR7817703 
 0.409354852 -2.253770083  1.696604663  1.477139664 -0.073483202 -0.414824888 
  SRR7817679   SRR3593580 
 0.821896899 -1.752570907 

$`R-MMU-1497770`
 SRR7817659  SRR7817662  SRR1636592  SRR1636589  SRR7817700  SRR7817675 
 1.26331509  1.06664582  1.22639418  1.43580290  0.14942995  0.62404409 
 SRR7817695  SRR7817699  SRR3593527  SRR7817616  SRR7817686  SRR7817626 
 0.23961535 -0.03401422  0.83560427  0.29509927  0.07045145  0.48703600 
 SRR7817671  SRR7817696  SRR1636588  SRR7817652  SRR1636593  SRR7817674 
 0.49548677  0.23956956  1.48167047  1.00098700  1.43183372  0.58110727 
 SRR4317609  SRR7817663  SRR7817661  SRR7817685  SRR1636586  SRR4317611 
 1.02122300  1.0810858

-1.47442160  0.61431013 -1.69843619 -1.04456682 -0.42480694 -0.70854530 
 SRR7817679  SRR3593580 
 0.13513942 -0.65880567 

$`R-MMU-9709109`
 SRR7817659  SRR7817662  SRR1636592  SRR1636589  SRR7817700  SRR7817675 
 1.26331509  1.06664582  1.22639418  1.43580290  0.14942995  0.62404409 
 SRR7817695  SRR7817699  SRR3593527  SRR7817616  SRR7817686  SRR7817626 
 0.23961535 -0.03401422  0.83560427  0.29509927  0.07045145  0.48703600 
 SRR7817671  SRR7817696  SRR1636588  SRR7817652  SRR1636593  SRR7817674 
 0.49548677  0.23956956  1.48167047  1.00098700  1.43183372  0.58110727 
 SRR4317609  SRR7817663  SRR7817661  SRR7817685  SRR1636586  SRR4317611 
 1.02122300  1.08108586  1.14304582  0.24407557  1.09990048  0.56165223 
 SRR3593525  SRR7817676  SRR7817684  SRR7817614  SRR7817623  SRR7817612 
 0.71644718  0.69505962 -0.28071885  0.61609554  1.09532956 -0.13063148 
 SRR7817698  SRR7817638  SRR7817647  SRR7817649  SRR7817664  SRR7817672 
 0.05303268  0.85112318  1.14940180  1.35495110  1.35983

 SRR7817695  SRR7817699  SRR3593527  SRR7817616  SRR7817686  SRR7817626 
-1.32807581 -0.98938574 -2.32870664 -1.93324783 -1.34563692 -1.31282304 
 SRR7817671  SRR7817696  SRR1636588  SRR7817652  SRR1636593  SRR7817674 
-1.48127472 -1.42334045 -3.03526322 -2.41107434 -2.41721654 -3.15269907 
 SRR4317609  SRR7817663  SRR7817661  SRR7817685  SRR1636586  SRR4317611 
-1.12432281 -0.78516411 -1.37397857 -1.39749930 -1.61990300 -2.02068349 
 SRR3593525  SRR7817676  SRR7817684  SRR7817614  SRR7817623  SRR7817612 
-2.63913740 -0.44704144 -1.40558962 -1.98334207 -2.04046249 -1.66885307 
 SRR7817698  SRR7817638  SRR7817647  SRR7817649  SRR7817664  SRR7817672 
-1.37463493 -1.75532528 -1.00895180 -1.00594506 -0.82723974 -1.12695260 
 SRR7817628  SRR1636591  SRR7817651  SRR1636590  SRR7817641  SRR4317658 
-1.61172422 -2.07641199 -2.29053458 -2.06190954  2.27118171  1.87290780 
 SRR7817693  SRR4317657  SRR7817680  SRR7817658  SRR7817645  SRR1636673 
 1.97834449  2.10968517  1.55528376  1.08526219  3.

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [53]:
%%R
# compare informaction content of below files with pca plots or similar
saveRDS(rxn_pca.nls, paste(OUT_DIR, "rxn_pca_nls030_time_cross_60.Rds", sep = ""))
saveRDS(vst.count.mtx.train,
        paste(OUT_DIR, "vst_count_mtx_train030_time_cross_60.Rds", sep = ""))

In [54]:
%%R
for (cv_fold in names(cv_fold_indices)) {
  cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
  print(cur_cv_fold_indices)
  print("----------")
}

[1]  4  8 29 39 50 56 65 74
[1] "----------"
[1] 10 22 27 37 43 46 49 59
[1] "----------"
[1]  6 26 33 38 52 62 64 75
[1] "----------"
[1] 13 16 30 34 41 45 78 79
[1] "----------"
[1]  2 11 28 35 66 67 70 73
[1] "----------"
[1]  1  7 12 25 51 58 72 76
[1] "----------"
[1] 18 24 31 32 53 55 61 68
[1] "----------"
[1]  9 15 17 36 47 60 69 80
[1] "----------"
[1]  3 19 20 21 44 54 63 77
[1] "----------"
[1]  5 14 23 40 42 48 57 71
[1] "----------"


In [ ]:
%%R
formatted_annotations <- format(binary_tcdd_dose_annotations, nsmall = 2)

formatted_annotations <- trimws(formatted_annotations)

binary_tcdd_dose_annotations <- formatted_annotations

print(binary_tcdd_dose_annotations)
for (annotation in binary_tcdd_dose_annotations) {
    print(annotation)
}

[1] "0.00"  "30.00"
[1] "0.00"
[1] "30.00"


In [ ]:
%%R
# main loop
for (rxn_id_idx in seq(1:length(rxns))) {
   rxn_id <- rxns[rxn_id_idx]
   ensembl_ids <- rxn2ensembls.nls[[rxn_id]]
   
   mean_misclass_rate <- list()
   sum_ari <- 0

   for (cv_fold in names(cv_fold_indices)) {
      cur_cv_fold_indices <- cv_fold_indices[[cv_fold]]
      
      vst.count.mtx.train.cv_train <-
         vst.count.mtx.train[, -cur_cv_fold_indices] # 4/5ths of training features
      vst.count.mtx.train.cv_test <-
         vst.count.mtx.train[, cur_cv_fold_indices] # 1/5th of training features
      
      tcdd_dose_detail.vec.train.cv_train <-
         tcdd_dose_detail.vec.train[-cur_cv_fold_indices] # 4/5ths of training labels
      tcdd_dose_detail.vec.train.cv_test <-
         tcdd_dose_detail.vec.train[cur_cv_fold_indices] # 1/5th of training labels
      
      binary_tcdd_dose_detail_vec.test.cv_test_list <- list()
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         binary_tcdd_dose_detail_vec.test.cv_test_list[[as.character(tissue_annotation)]] <-
            (as.character(tcdd_dose_detail.vec.train.cv_test) == as.character(tissue_annotation))
      }
      
      cv_train.expr_mat <-
         t(vst.count.mtx.train.cv_train[ensembl_ids, ])
      cv_test.expr_mat <-
         t(vst.count.mtx.train.cv_test[ensembl_ids, ])
      
      rxn_knn_calls <- class::knn(train = cv_train.expr_mat,
                                  test = cv_test.expr_mat,
                                  cl = tcdd_dose_detail.vec.train.cv_train)
      
      # calculate & store adjusted rand index
      cur_ari <- pdfCluster::adj.rand.index(rxn_knn_calls,
                                            tcdd_dose_detail.vec.train.cv_test)
      sum_ari <- cur_ari + sum_ari
      
      # for each tissue, calculate misclassification rate
      for (tissue_annotation in binary_tcdd_dose_annotations) {
         cur_rxn_knn_calls <- (rxn_knn_calls == tissue_annotation)
            
         # calculate misclassification rate (https://stat.ethz.ch/pipermail/r-help/2011-September/288885.html)
         tab <- table(cur_rxn_knn_calls,
                      binary_tcdd_dose_detail_vec.test.cv_test_list[[tissue_annotation]])
        # print(tab)
         cur_misclass_rate <- 1 - sum(diag(tab)) / sum(tab)
        # print(paste("Misclass rate = 1 - ",sum(diag(tab))," / ",sum(tab)," = ", cur_misclass_rate,"...",sep=""))
         sum_misclass_rate <- cur_misclass_rate
         if (!is.null(mean_misclass_rate[[tissue_annotation]])) {
           sum_misclass_rate <- sum_misclass_rate + mean_misclass_rate[[tissue_annotation]]
         }
         mean_misclass_rate[[tissue_annotation]] <- sum_misclass_rate
      }
   }
   for(tissue_annotation in binary_tcdd_dose_annotations){
      mean_misclass_rate[[tissue_annotation]] <- (mean_misclass_rate[[tissue_annotation]] / N_FOLDS)
   }
   mean_ari <- sum_ari / N_FOLDS
   ecount <- length(ensembl_ids)
   
   rxn_knn_misclass_rate.nls[[rxn_id]] <- mean_misclass_rate
   assign("mean_misclass_rate",NULL,envir = .GlobalEnv)
   
   rxn_knn_ari.nls[[rxn_id]] <- mean_ari
   rxn_knn_ecount.nls[[rxn_id]] <- ecount
   
   count <- count + 1
   if (mod(count, 10) == 0) {
      print(
         paste(
            "Last RXN_ID = ",
            rxn_id,
            ": Last ARI = ",
            mean_ari,
            ": Last ECOUNT = ",
            ecount,
            ": Last Lung MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Lung"]],
            ": Last Uterus MISCLASS = ",
            rxn_knn_misclass_rate.nls[[rxn_id]][["Uterus"]],
            ". Now ",
            round(1.0 - count / length(rxns),3) * 100,
            "% remaining..."
         )
      )
      flush.console()
   }
}

[1] "Last RXN_ID =  R-MMU-749456 : Last ARI =  1 : Last ECOUNT =  178 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9021601 : Last ARI =  1 : Last ECOUNT =  24 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3108203 : Last ARI =  1 : Last ECOUNT =  15 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-9838627 : Last ARI =  0.777984536082474 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-193679 : Last ARI =  -0.00700515463917523 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-194544 : Last ARI =  0.152963917525773 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  99.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-3247837 : Last ARI =  0.9494

[1] "Last RXN_ID =  R-MMU-6791222 : Last ARI =  1 : Last ECOUNT =  61 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9696268 : Last ARI =  1 : Last ECOUNT =  41 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-1912394 : Last ARI =  1 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-8936481 : Last ARI =  1 : Last ECOUNT =  77 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-9677051 : Last ARI =  1 : Last ECOUNT =  10 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5336403 : Last ARI =  1 : Last ECOUNT =  72 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  94.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-72671 : Last ARI =  0.814969072164949 : Last ECOUNT =  90 : Last Lung MISCL

[1] "Last RXN_ID =  R-MMU-174224 : Last ARI =  0.949484536082474 : Last ECOUNT =  18 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-3788708 : Last ARI =  0.949484536082474 : Last ECOUNT =  23 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-927830 : Last ARI =  0.949484536082474 : Last ECOUNT =  11 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-448955 : Last ARI =  0.848453608247423 : Last ECOUNT =  6 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  89 % remaining..."
[1] "Last RXN_ID =  R-MMU-200652 : Last ARI =  0.0951718213058419 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  88.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-9624798 : Last ARI =  0.20169587628866 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  88.8 % remaining..."
[1] "Last RXN

[1] "Last RXN_ID =  R-MMU-9818576 : Last ARI =  0.247872852233677 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  84 % remaining..."
[1] "Last RXN_ID =  R-MMU-2029273 : Last ARI =  0.949484536082474 : Last ECOUNT =  71 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-8850356 : Last ARI =  0.898969072164948 : Last ECOUNT =  11 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-1363303 : Last ARI =  1 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-188386 : Last ARI =  0.949484536082474 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-390593 : Last ARI =  0.949484536082474 : Last ECOUNT =  35 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  83.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2

[1] "Last RXN_ID =  R-MMU-211910 : Last ARI =  1 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.8 % remaining..."
[1] "Last RXN_ID =  R-MMU-3928646 : Last ARI =  0.814969072164949 : Last ECOUNT =  12 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.7 % remaining..."
[1] "Last RXN_ID =  R-MMU-8848484 : Last ARI =  0.74020618556701 : Last ECOUNT =  5 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9022185 : Last ARI =  0.663422680412371 : Last ECOUNT =  3 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2032396 : Last ARI =  0.454721649484536 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-182990 : Last ARI =  1 : Last ECOUNT =  21 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  78.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-448421 : Last AR

...

[1] "Last RXN_ID =  R-MMU-77342 : Last ARI =  0.335974226804124 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-449937 : Last ARI =  -0.0416563573883161 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-9718020 : Last ARI =  0.265742268041237 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-6806966 : Last ARI =  0.360458762886598 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-140783 : Last ARI =  0.949484536082474 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5696457 : Last ARI =  0.579422680412371 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  22.1 % remaining..."
[1] "Last RX

[1] "Last RXN_ID =  R-MMU-9653592 : Last ARI =  0.00324226804123711 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.6 % remaining..."
[1] "Last RXN_ID =  R-MMU-9668464 : Last ARI =  0.0212474226804124 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-2454118 : Last ARI =  0.639969072164948 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-159425 : Last ARI =  1 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-6785607 : Last ARI =  0.663422680412371 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-6807224 : Last ARI =  0.215554982817869 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  17 % remaining..."
[1] "Last RXN_ID =  R-MMU-

[1] "Last RXN_ID =  R-MMU-9027532 : Last ARI =  0.764453608247423 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.5 % remaining..."
[1] "Last RXN_ID =  R-MMU-917888 : Last ARI =  0.515721649484536 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-6800315 : Last ARI =  0.280912371134021 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-200424 : Last ARI =  0.243175257731959 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-425822 : Last ARI =  -0.00292439862542953 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-8848873 : Last ARI =  0.468469072164948 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  12 % remaining..."
[1] "Last RX

[1] "Last RXN_ID =  R-MMU-139909 : Last ARI =  0.04156529209622 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.4 % remaining..."
[1] "Last RXN_ID =  R-MMU-8851979 : Last ARI =  0.26420618556701 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-9704248 : Last ARI =  0.663422680412371 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-5629230 : Last ARI =  0.848453608247423 : Last ECOUNT =  4 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-1482961 : Last ARI =  0.217524054982818 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  7 % remaining..."
[1] "Last RXN_ID =  R-NUL-9830947 : Last ARI =  0.485737113402062 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  6.9 % remaining..."
[1] "Last RXN_ID =  R

[1] "Last RXN_ID =  R-MMU-6807055 : Last ARI =  0.680453608247423 : Last ECOUNT =  1 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.3 % remaining..."
[1] "Last RXN_ID =  R-MMU-1462039 : Last ARI =  0.663422680412371 : Last ECOUNT =  9 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.2 % remaining..."
[1] "Last RXN_ID =  R-MMU-3341294 : Last ARI =  0.275427835051546 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2.1 % remaining..."
[1] "Last RXN_ID =  R-MMU-8952128 : Last ARI =  0.811469072164948 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  2 % remaining..."
[1] "Last RXN_ID =  R-MMU-9606623 : Last ARI =  0.508953608247423 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  1.9 % remaining..."
[1] "Last RXN_ID =  R-MMU-6814096 : Last ARI =  0.479786941580756 : Last ECOUNT =  2 : Last Lung MISCLASS =   : Last Uterus MISCLASS =   . Now  1.8 % remaining..."
[1] "Last RXN_ID =

In [57]:
%%R
saveRDS(
   rxn_knn_misclass_rate.nls,
   paste(OUT_DIR, "toi_rxn_knn_misclass_rate_nls030_time_cross_60.Rds", sep = "")
)
saveRDS(rxn_knn_ari.nls,
        paste(OUT_DIR, "toi_rxn_knn_ari_nls030_time_cross_60.Rds", sep = ""))
saveRDS(rxn_knn_ecount.nls,
        paste(OUT_DIR, "toi_rxn_knn_ecount_nls030_time_cross_60.Rds", sep = ""))

In [58]:
%%R
d <- data.frame(
   RXN_ID = names(rxn2ensembls.nls),
   MISCLASS = unlist(rxn_knn_misclass_rate.nls),
   ARI = unlist(rxn_knn_ari.nls),
   ECOUNT = unlist(rxn_knn_ecount.nls)
)
print(d)
saveRDS(d, paste(OUT_DIR, "toi_summary_df030_time_cross_60.Rds", sep = ""))

                           RXN_ID MISCLASS           ARI ECOUNT
R-MMU-170666.0.00    R-MMU-170666        0  1.000000e+00     14
R-MMU-170666.30.00   R-MMU-170671        0  1.000000e+00     14
R-MMU-170671.0.00    R-MMU-170674        0  1.000000e+00     14
R-MMU-170671.30.00   R-MMU-170686        0  1.000000e+00     14
R-MMU-170674.0.00    R-MMU-380073        0  1.000000e+00    182
R-MMU-170674.30.00   R-MMU-392187        0  1.000000e+00     22
R-MMU-170686.0.00    R-MMU-392195        0  1.000000e+00     22
R-MMU-170686.30.00   R-MMU-392202        0  1.000000e+00     22
R-MMU-380073.0.00    R-MMU-749454        0  1.000000e+00    178
R-MMU-380073.30.00   R-MMU-749456        0  1.000000e+00    178
R-MMU-392187.0.00    R-MMU-751001        0  1.000000e+00     21
R-MMU-392187.30.00  R-MMU-8964229        0  1.000000e+00      5
R-MMU-392195.0.00   R-MMU-8964242        0  1.000000e+00      5
R-MMU-392195.30.00  R-MMU-8964329        0  1.000000e+00      5
R-MMU-392202.0.00   R-MMU-8982012       

R-MMU-205099.30.00  R-MMU-5654224        0  1.000000e+00     12
R-MMU-205112.0.00   R-MMU-5654392        0  1.000000e+00     20
R-MMU-205112.30.00  R-MMU-5654397        0  1.000000e+00     16
R-MMU-205117.0.00   R-MMU-5654399        0  1.000000e+00     16
R-MMU-205117.30.00  R-MMU-5654402        0  1.000000e+00     20
R-MMU-209532.0.00   R-MMU-5654404        0  1.000000e+00     16
R-MMU-209532.30.00  R-MMU-5654406        0  1.000000e+00     18
R-MMU-209566.0.00   R-MMU-5654407        0  1.000000e+00     16
R-MMU-209566.30.00  R-MMU-5654408        0  1.000000e+00     12
R-MMU-9012761.0.00  R-MMU-5654409        0  1.000000e+00     12
R-MMU-9012761.30.00 R-MMU-5654413        0  1.000000e+00     17
R-MMU-3247837.0.00  R-MMU-5654416        0  1.000000e+00     15
R-MMU-3247837.30.00 R-MMU-5654418        0  1.000000e+00     14
R-MMU-3247840.0.00  R-MMU-5654422        0  1.000000e+00     14
R-MMU-3247840.30.00 R-MMU-5654423        0  1.000000e+00     16
R-MMU-3247843.0.00  R-MMU-5654425       

R-MMU-5654224.30.00 R-MMU-9011082        0  5.389381e-01      2
R-MMU-5654392.0.00  R-MMU-9011144        0  1.539948e-01      3
R-MMU-5654392.30.00 R-MMU-9011146        0  1.539948e-01      3
R-MMU-5654397.0.00  R-MMU-9753028        0  5.254072e-01      5
R-MMU-5654397.30.00 R-MMU-9753126        0  5.254072e-01      5
R-MMU-5654399.0.00   R-MMU-514604        0  6.634227e-01      2
R-MMU-5654399.30.00  R-MMU-975389        0  7.412371e-01      4
R-MMU-5654402.0.00  R-MMU-1169394        0  8.654845e-01      5
R-MMU-5654402.30.00 R-MMU-1169398        0  6.804536e-01      5
R-MMU-5654404.0.00  R-MMU-1169402        0  7.814845e-01      6
R-MMU-5654404.30.00 R-MMU-1169403        0  5.794227e-01      4
R-MMU-5654406.0.00  R-MMU-1169405        0  9.160000e-01      5
R-MMU-5654406.30.00 R-MMU-1169406        0  1.000000e+00     12
R-MMU-5654407.0.00  R-MMU-1678842        0  9.494845e-01     13
R-MMU-5654407.30.00 R-MMU-1678843        0  7.139381e-01      5
R-MMU-5654408.0.00  R-MMU-5653754       

R-MMU-5654659.30.00 R-MMU-2424487        0  1.000000e+00     22
R-MMU-5654662.0.00   R-MMU-388814        0  7.979381e-01      6
R-MMU-5654662.30.00  R-MMU-388829        0  1.000000e+00      9
R-MMU-5654663.0.00   R-MMU-388831        0  1.000000e+00      8
R-MMU-5654663.30.00  R-MMU-388832        0  1.000000e+00      9
R-MMU-5654664.0.00   R-MMU-388833        0  1.000000e+00     17
R-MMU-5654664.30.00  R-MMU-389158        0  1.000000e+00      9
R-MMU-5654667.0.00   R-MMU-389348        0  9.494845e-01      8
R-MMU-5654667.30.00  R-MMU-389350        0  9.494845e-01      8
R-MMU-5654669.0.00   R-MMU-389352        0  9.494845e-01      7
R-MMU-5654669.30.00  R-MMU-389354        0  9.494845e-01      7
R-MMU-5654672.0.00   R-MMU-389381        0  8.484536e-01      6
R-MMU-5654672.30.00  R-MMU-389758        0  1.000000e+00     22
R-MMU-5654673.0.00   R-MMU-389759        0  7.644536e-01      7
R-MMU-5654673.30.00  R-MMU-389762        0  7.989691e-01      5
R-MMU-5654677.0.00   R-MMU-434836       

R-MMU-9011082.30.00 R-MMU-9692139        0  2.429742e-01      2
R-MMU-9011144.0.00  R-MMU-9692145        0  5.759227e-01      2
R-MMU-9011144.30.00 R-MMU-9692156        0  3.099433e-01      4
R-MMU-9011146.0.00  R-MMU-9692157        0  3.099433e-01      4
R-MMU-9011146.30.00 R-MMU-9692268        0  2.032268e-01      2
R-MMU-9753028.0.00   R-MMU-450434        0  4.612526e-01      1
R-MMU-9753028.30.00  R-MMU-450466        0  9.160000e-01     45
R-MMU-9753126.0.00   R-MMU-450551        0  8.989691e-01      7
R-MMU-9753126.30.00  R-MMU-450580        0  9.494845e-01     12
R-MMU-514604.0.00     R-MMU-72103        0  1.000000e+00     43
R-MMU-514604.30.00  R-MMU-9770119        0  1.000000e+00     69
R-MMU-975389.0.00   R-MMU-9770141        0  1.000000e+00    123
R-MMU-975389.30.00  R-MMU-9770142        0  1.000000e+00    132
R-MMU-1169394.0.00  R-MMU-9770145        0  1.000000e+00    145
R-MMU-1169394.30.00 R-MMU-9770236        0  1.000000e+00    119
R-MMU-1169398.0.00  R-MMU-6798748       

...

R-MMU-1640164.0.00  R-MMU-2395872        0  3.836753e-01      1
R-MMU-1640164.30.00 R-MMU-9731228        0  3.836753e-01      1
R-MMU-9766551.0.00  R-MMU-9731590        0  3.836753e-01      1
R-MMU-9766551.30.00 R-MMU-9731613        0  3.836753e-01      1
R-MMU-442422.0.00   R-MMU-9731632        0  3.836753e-01      1
R-MMU-442422.30.00   R-MMU-426520        0  4.814433e-01      1
R-MMU-8874364.0.00  R-MMU-5578712        0  8.114691e-01      2
R-MMU-8874364.30.00 R-MMU-5578965        0  3.847062e-01      2
R-MMU-8936519.0.00  R-MMU-5578966        0  3.847062e-01      2
R-MMU-8936519.30.00 R-MMU-9023912        0  4.814433e-01      1
R-MMU-1482745.0.00  R-MMU-9820843        0  4.814433e-01      1
R-MMU-1482745.30.00 R-MMU-9820863        0  4.814433e-01      1
R-MMU-1482771.0.00  R-MMU-1299318        0  2.612113e-01      2
R-MMU-1482771.30.00 R-MMU-6786720        0  4.687062e-01      1
R-MMU-1482828.0.00  R-MMU-8851538        0  1.000000e+00      1
R-MMU-1482828.30.00 R-MMU-8851550       

R-MMU-9749792.0.00   R-MMU-193746        0  7.644536e-01      1
R-MMU-9749792.30.00  R-MMU-193755        0  7.644536e-01      1
R-MMU-5696119.0.00   R-MMU-193821        0  7.644536e-01      1
R-MMU-5696119.30.00  R-MMU-193824        0  7.644536e-01      1
R-MMU-9673827.0.00  R-NUL-1236960        0  7.139381e-01      1
R-MMU-9673827.30.00 R-MMU-8874239        0  5.289072e-01      2
R-MMU-2872444.0.00  R-MMU-8874322        0 -1.950515e-02      1
R-MMU-2872444.30.00 R-MMU-8874406        0 -1.950515e-02      1
R-MMU-204617.0.00   R-MMU-6814086        0  3.604588e-01      3
R-MMU-204617.30.00  R-MMU-6814088        0  7.798969e-02      2
R-MMU-204647.0.00   R-MMU-5619426        0  3.699485e-02      1
R-MMU-204647.30.00  R-MMU-8848023        0  7.979381e-01      2
R-MMU-204662.0.00   R-MMU-8848077        0  7.979381e-01      2
R-MMU-204662.30.00  R-MMU-8848110        0  5.929536e-01      2
R-MMU-1482932.0.00  R-MMU-8848774        0  6.804536e-01      2
R-MMU-1482932.30.00 R-MMU-8848776       

R-MMU-202709.0.00   R-MMU-5629230        0  8.484536e-01      4
R-MMU-202709.30.00  R-MMU-8942575        0  4.214536e-01      2
R-MMU-1254248.0.00  R-MMU-8953339        0  3.980241e-01      1
R-MMU-1254248.30.00 R-MMU-5696839        0  1.572423e-01      1
R-MMU-1254251.0.00  R-MMU-6801456        0  1.572423e-01      1
R-MMU-1254251.30.00 R-MMU-8944219        0  4.954227e-01      1
R-MMU-2032770.0.00   R-MMU-879594        0  6.391753e-01      1
R-MMU-2032770.30.00  R-MMU-211874        0  3.487113e-01      1
R-MMU-2032775.0.00   R-MMU-350604        0  7.309691e-01      1
R-MMU-2032775.30.00  R-MMU-373717        0  2.225550e-01      2
R-MMU-163320.0.00   R-MMU-1482961        0  2.175241e-01      1
R-MMU-163320.30.00  R-MMU-1482962        0  3.519588e-01      2
R-MMU-8851988.0.00   R-MMU-264418        0  3.258076e-02      1
R-MMU-8851988.30.00  R-MMU-264435        0  5.984742e-01      2
R-MMU-6813749.0.00  R-MMU-4167511        0  5.056907e-01      2
R-MMU-6813749.30.00 R-MMU-5635102       

R-MMU-708349.0.00   R-MMU-9014678        0  1.580601e-01      2
R-MMU-708349.30.00   R-MMU-162873        0  4.397113e-01      1
R-MMU-6798474.0.00  R-MMU-8878914        0  3.151907e-01      1
R-MMU-6798474.30.00 R-MMU-8858270        0  7.239691e-01      1
R-MMU-6798528.0.00  R-MMU-5605262        0  7.509107e-02      1
R-MMU-6798528.30.00  R-MMU-444620        0  6.804536e-01      2
R-MMU-9844860.0.00  R-MMU-9009950        0  4.082818e-02      1
R-MMU-9844860.30.00 R-MMU-8937744        0  3.854433e-01      1
R-MMU-446185.0.00   R-MMU-8937767        0  3.854433e-01      1
R-MMU-446185.30.00   R-MMU-914067        0  7.104381e-01      2
R-MMU-9706330.0.00  R-MMU-9604980        0  5.467560e-01      2
R-MMU-9706330.30.00 R-MMU-9606789        0  7.814845e-01      3
R-MMU-8944218.0.00  R-MMU-8870352        0  3.827371e-01      1
R-MMU-8944218.30.00 R-MMU-8870354        0  3.827371e-01      1
R-MMU-111881.0.00    R-MMU-419428        0  9.494845e-01      4
R-MMU-111881.30.00  R-MMU-3296301       

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [59]:
%%R
pid <- read.table(paste(OUT_DIR,"tcdd_project_id030_time_cross_60.txt",sep=""),header=FALSE)
sid <- read.table(paste(OUT_DIR,"tcdd_sample_id030_time_cross_60.txt",sep=""), header=FALSE)
print(sid)

           V1
1  SRR7817651
2  SRR7817676
3  SRR7817687
4  SRR7817635
5  SRR7817696
6  SRR7817639
7  SRR7817699
8  SRR4317611
9  SRR7817627
10 SRR7817616
11 SRR3593524
12 SRR1636588
13 SRR7817640
14 SRR7817688
15 SRR7817662
16 SRR3593527
17 SRR4317610
18 SRR7817685
19 SRR1636590
20 SRR7817686
21 SRR4317612
22 SRR7817649
23 SRR7817615
24 SRR1636589
25 SRR3593526
26 SRR3593523
27 SRR7817697
28 SRR7817613
29 SRR7817636
30 SRR7817683
31 SRR7817647
32 SRR7817612
33 SRR7817672
34 SRR3593525
35 SRR7817684
36 SRR7817652
37 SRR7817664
38 SRR7817675
39 SRR7817626
40 SRR7817698
41 SRR3593580
42 SRR1636672
43 SRR4317655
44 SRR7817620
45 SRR7817682
46 SRR4317657
47 SRR7817655
48 SRR3593575
49 SRR4317659
50 SRR1636675
51 SRR7817678
52 SRR3593577
53 SRR7817657
54 SRR7817617
55 SRR7817619
56 SRR7817631
57 SRR3593573
58 SRR7817641
59 SRR7817629
60 SRR7817653
61 SRR7817706
62 SRR7817666
63 SRR3593579
64 SRR4317660
65 SRR7817701
66 SRR7817618
67 SRR7817670
68 SRR7817665
69 SRR7817632
70 SRR7817692
71 SRR

In [ ]:
%%R
library(htmlwidgets)
min_misclass_pca <-
   prcomp(t(vst.count.mtx.train), scale. = T)
pca.d <- data.frame(
   PC1 = min_misclass_pca$x[, 1],
   PC2 = min_misclass_pca$x[, 2],
   PC3 = min_misclass_pca$x[, 3],
   Section = tcdd_dose_detail.vec.train,
   Project_id = pid$V1,
   Sample_id = sid$V1
)

ggplot(pca.d, aes(x = PC1, y = PC2, colour = Section)) +
   geom_point(size = 3) + 
   geom_text(aes(label = paste(Project_id, Sample_id)), vjust = -1, hjust = 1, size = 2) +  
   scale_colour_manual(values = c("0" = "red", "30" = "green")) +  
   theme_bw()

p <- plot_ly(
   data = pca.d,
   x = ~PC1,
   y = ~PC2,
   z = ~PC3,
   type = "scatter3d",
   mode = "markers",
   marker = list(
     color = as.factor(pca.d$Section),  
     colors = c("red", "green"), 
     size = 5
   ),
   text = ~paste("Project ID:", Project_id, "Sample ID:", Sample_id)  
)
saveWidget(p, "plotly_chart030_time_cross_60.html", selfcontained = TRUE)